In [1]:
import time as tm
import pandas as pd
import numpy as np
import geopy as geopy
from geopy.geocoders import Nominatim
from folium.plugins import HeatMap
import folium # map rendering library
import branca.colormap as cm

from sklearn.cluster import KMeans

print(f"Pandas version: {pd.__version__}")

Pandas version: 1.2.4


In [2]:
df_districts = pd.read_csv('../data/districts.csv', index_col=0)
df_districts

Name              Name_rus  Population  \
0                  Aeroport              Аэропорт       74775   
1                   Begovoy               Беговой       44385   
2            Beskudnikovsky       Бескудниковский       74790   
3                Dmitrovsky           Дмитровский       88931   
4                Golovinsky           Головинский      102160   
..                      ...                   ...         ...   
113  Pokrovskoye-Streshnevo  Покровское-Стрешнево       46707   
114        Severnoe Tushino       Северное Тушино      138533   
115               Shchukino                Щукино       89454   
116                Strogino              Строгино      124149   
117        Yuzhnoye Tushino          Южное Тушино       93444   

                                           Coordinates  Num_stations  \
0    [[37.51101, 55.80608], [37.51137, 55.80647], [...             0   
1    [[37.54084, 55.78496], [37.54188, 55.78541], [...             0   
2    [[37.52966, 55.87283], [37.52982, 55.87291], [...             1   
3    [[37.49625, 55.89248], [37.49851, 55.89347], [...             0   
4    [[37.46446, 55.84712], [37.46569, 55.84756], [...             1   
..                                                 ...           ...   
113  [[37.39444, 55.8291], [37.395, 55.83041], [37....             1   
114  [[37.39374, 55.85179], [37.39505, 55.85432], [...             0   
115  [[37.4461, 55.79449], [37.44618, 55.79531], [3...             0   
116  [[37.36726, 55.79036], [37.36784, 55.79136], [...             0   
117  [[37.39182, 55.84723], [37.39187, 55.84762], [...             2   

     Cost per meter  Free_power  Power_per_person  
0            207200   83.666667          0.001119  
1            231700   18.000000          0.000406  
2            132700   37.716000          0.000504  
3            132700   37.716000          0.000424  
4            154400   37.716000          0.000369  
..              ...         ...               ...  
113          169900   18.435000          0.000395  
114          155200   46.140000          0.000333  
115          169900   29.500000          0.000330  
116          167400   18.435000          0.000148  
117          155200   46.140000          0.000494  

[118 rows x 8 columns]

In [3]:
df_ev = pd.read_csv('../data/el_infostructure.csv', index_col=0)
df_ev

id            class tags                    name_ru  \
0    194014721       substation   {}                        NaN   
1    194014711       substation   {}                        NaN   
2    193841447       substation   {}                        NaN   
3    193841032       substation   {}                        NaN   
4    193841446       substation   {}                        NaN   
..         ...              ...  ...                        ...   
995  194162573      power_plant   {}  ГЭС-1 им. П. Г. Смидовича   
996  194167338  power_generator   {}                        NaN   
997  194161352      power_plant   {}          Карамышевская ГЭС   
998  194162584      power_plant   {}        ТЭС "Международная"   
999  194162440      power_plant   {}                     ТЭЦ-12   

            operator                                            tags_ru  \
0                NaN  {'Напряжения': None, 'Газовая изоляция': 'неиз...   
1                NaN  {'Напряжения': None, 'Газовая изоляция': 'неиз...   
2                NaN  {'Напряжения': None, 'Газовая изоляция': 'неиз...   
3                NaN  {'Напряжения': None, 'Газовая изоляция': 'неиз...   
4                NaN  {'Напряжения': None, 'Газовая изоляция': 'неиз...   
..               ...                                                ...   
995  ПАО «Мосэнерго»  {'Выработка горячего воздуха': None, 'Выработк...   
996              NaN  {'Выработка горячего воздуха': None, 'Выработк...   
997              NaN  {'Выработка горячего воздуха': None, 'Выработк...   
998              NaN  {'Выработка горячего воздуха': None, 'Выработк...   
999  ОАО "Мосэнерго"  {'Выработка горячего воздуха': None, 'Выработк...   

     opening_hours        class_ru         addr_region  addr_district  ...  \
0              NaN      Подстанция              Москва            NaN  ...   
1              NaN      Подстанция              Москва            NaN  ...   
2              NaN      Подстанция  Московская область            NaN  ...   
3              NaN      Подстанция  Московская область            NaN  ...   
4              NaN      Подстанция  Московская область            NaN  ...   
..             ...             ...                 ...            ...  ...   
995            NaN  Электростанция              Москва            NaN  ...   
996            NaN       Генератор              Москва            NaN  ...   
997            NaN  Электростанция              Москва            NaN  ...   
998            NaN  Электростанция              Москва            NaN  ...   
999            NaN  Электростанция              Москва            NaN  ...   

     addr_house                                             c_geom  \
0           NaN  0101000020E610000006789EBA27D14240BB959C016DE4...   
1         10 с4  0101000020E6100000F8B8BB83A7CD42403395E50A21DC...   
2           NaN  0101000020E61000006A9DBD529BEE4240F83A9092DFDF...   
3           NaN  0101000020E6100000D6A0D4038BF24240FA6A589D66E5...   
4           NaN  0101000020E61000009BBDD820B8EE42403F834D9DC7DF...   
..          ...                                                ...   
995         NaN  0101000020E6100000E6B6BDF2C0D04240DD1D85D2B9DF...   
996         NaN  0101000020E6100000CB9D9960B8D84240760E65A80ADF...   
997         NaN  0101000020E610000017486A7A9DBB4240EA43787C9EE1...   
998         NaN  0101000020E6100000BC33B415A7C342406585C89158E1...   
999         NaN  0101000020E6100000ACA962B343C7424046F17DDF30DE...   

             addr_country  email  description               wikipedia  \
0    Российская Федерация    NaN          NaN                     NaN   
1    Российская Федерация    NaN          NaN                     NaN   
2    Российская Федерация    NaN          NaN                     NaN   
3    Российская Федерация    NaN          NaN                     NaN   
4    Российская Федерация    NaN          NaN                     NaN   
..                    ...    ...          ...                     ...   
995  Российская Ф

In [4]:
kclusters = 3

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=91).fit(df_districts[['Population', 'Cost per meter', 'Free_power', 'Power_per_person']])

In [5]:
kmeans.labels_[0:10] 

array([0, 1, 0, 2, 2, 0, 0, 0, 0, 0], dtype=int32)

In [6]:
df_districts.insert(0, 'Cluster', kmeans.labels_)
df_districts

Cluster                    Name              Name_rus  Population  \
0          0                Aeroport              Аэропорт       74775   
1          1                 Begovoy               Беговой       44385   
2          0          Beskudnikovsky       Бескудниковский       74790   
3          2              Dmitrovsky           Дмитровский       88931   
4          2              Golovinsky           Головинский      102160   
..       ...                     ...                   ...         ...   
113        0  Pokrovskoye-Streshnevo  Покровское-Стрешнево       46707   
114        2        Severnoe Tushino       Северное Тушино      138533   
115        0               Shchukino                Щукино       89454   
116        2                Strogino              Строгино      124149   
117        2        Yuzhnoye Tushino          Южное Тушино       93444   

                                           Coordinates  Num_stations  \
0    [[37.51101, 55.80608], [37.51137, 55.80647], [...             0   
1    [[37.54084, 55.78496], [37.54188, 55.78541], [...             0   
2    [[37.52966, 55.87283], [37.52982, 55.87291], [...             1   
3    [[37.49625, 55.89248], [37.49851, 55.89347], [...             0   
4    [[37.46446, 55.84712], [37.46569, 55.84756], [...             1   
..                                                 ...           ...   
113  [[37.39444, 55.8291], [37.395, 55.83041], [37....             1   
114  [[37.39374, 55.85179], [37.39505, 55.85432], [...             0   
115  [[37.4461, 55.79449], [37.44618, 55.79531], [3...             0   
116  [[37.36726, 55.79036], [37.36784, 55.79136], [...             0   
117  [[37.39182, 55.84723], [37.39187, 55.84762], [...             2   

     Cost per meter  Free_power  Power_per_person  
0            207200   83.666667          0.001119  
1            231700   18.000000          0.000406  
2            132700   37.716000          0.000504  
3            132700   37.716000          0.000424  
4            154400   37.716000          0.000369  
..              ...         ...               ...  
113          169900   18.435000          0.000395  
114          155200   46.140000          0.000333  
115          169900   29.500000          0.000330  
116          167400   18.435000          0.000148  
117          155200   46.140000          0.000494  

[118 rows x 9 columns]

In [7]:
for i in range(kclusters):
    count = df_districts['Cluster'].value_counts()[i]
    print(f'Cluster \'{i+1}\' has {count} Neighobrhoods')

Cluster '1' has 63 Neighobrhoods
Cluster '2' has 12 Neighobrhoods
Cluster '3' has 43 Neighobrhoods


Power per person

In [8]:
geolocator = Nominatim(user_agent="ny_explorer")
address = 'Moscow'
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

moscow_map = folium.Map(location=[latitude, longitude], zoom_start=10)

mo_geo = r'../data/_mo.geojson'

choropleth = folium.Choropleth(
    geo_data=mo_geo,
    data=df_districts,
    columns=['Name_rus', 'Power_per_person'],
    key_on='properties.NAME',
    fill_color='YlGnBu', 
    fill_opacity=0.7, 
    line_opacity=0.9,
    highlight=True,
    legend_name='Moscow districts'
)

choropleth.add_to(moscow_map)
    
style_function = "font-size: 15px; font-weight: bold"
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['NAME'], style=style_function, labels=False))
    
moscow_map

The geograpical coordinate of Moscow are 55.7504461, 37.6174943.


Cluster

In [9]:
geolocator = Nominatim(user_agent="ny_explorer")
address = 'Moscow'
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

moscow_map = folium.Map(location=[latitude, longitude], zoom_start=10)

mo_geo = r'../data/_mo.geojson'

choropleth = folium.Choropleth(
    geo_data=mo_geo,
    data=df_districts,
    columns=['Name_rus', 'Power_per_person'],
    key_on='properties.NAME',
    fill_color='YlGnBu', 
    fill_opacity=0.7, 
    line_opacity=0.9,
    highlight=True,
    legend_name='Moscow districts'
)

choropleth.add_to(moscow_map)
    
style_function = "font-size: 15px; font-weight: bold"
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['NAME'], style=style_function, labels=False))
    
moscow_map

The geograpical coordinate of Moscow are 55.7504461, 37.6174943.


In [10]:
moscow_map.save('heatmap.html')

In [13]:
geolocator = Nominatim(user_agent="ny_explorer")
address = 'Moscow'
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

moscow_map = folium.Map(location=[latitude, longitude], zoom_start=10)

mo_geo = r'../data/_mo.geojson'

choropleth = folium.Choropleth(
    geo_data=mo_geo,
    data=df_districts,
    columns=['Name_rus', 'Cluster'],
    key_on='properties.NAME',
    fill_color='YlGnBu', 
    fill_opacity=0.7, 
    line_opacity=0.9,
    highlight=True,
    legend_name='Moscow districts'
)

choropleth.add_to(moscow_map)
    
style_function = "font-size: 15px; font-weight: bold"
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['NAME'], style=style_function, labels=False))
    
# Add legend and show map
legend_html = """
<div style="position:fixed;
     bottom: 20px; 
     left: 20px; 
     width: 170px; 
     height:90px; 
     border:2px solid grey;
     background-color: lightgrey;
     z-index: 9999;
     font-size:14px;">
     &nbsp;<b>Кластеры:</b><br>
     &nbsp;<i class="fa fa-circle fa-1x" style="color:rgba(15.5,  179.9,  212.5,   1)"></i>&nbsp;Зарядки 1 типа<br>
     &nbsp;<i class="fa fa-circle fa-1x" style="color:rgba(50.5, 0,      200, 1)"></i>&nbsp;Зарядки 1 и 2 типа<br>
     &nbsp;<i class="fa fa-circle fa-1x" style="color:rgba(255,  255,  200, 1)"></i>&nbsp;Зарядки 2 типа<br>
</div>"""

moscow_map.get_root().html.add_child(folium.Element(legend_html))    

moscow_map

The geograpical coordinate of Moscow are 55.7504461, 37.6174943.


In [14]:
moscow_map.save('clusters_map.html')